In [1]:
! pip -q install pandas plotly
! pip -q install nbformat
! pip -q install kaleido

In [2]:
import pandas as pd
import plotly.express as px
#import kaleido
import plotly.graph_objects as go
import plotly.colors as pc
import glob
import json
from plotly.subplots import make_subplots
import math
import os
import numpy as np
import plotly.io as pio
pio.kaleido.scope.mathjax = None

# Reading the results

In [3]:
result_files = glob.glob("eval_results/fineweb/*/*_iter_*/*.json")
#baseline_hptl2_dedup = glob.glob("/scratch/project_462000353/pyysalos/second-hplt-eval/eval_results/results/hplt_v2_dedup_iter_00*/*.json")
#baseline_fineweb = glob.glob("/scratch/project_462000353/pyysalos/second-hplt-eval/eval_results/results/fineweb_iter_00*/*.json")

tasks = {"custom|arc:easy|0":"arc_easy",
         "custom|arc:challenge|0":"arc_challenge",
         "custom|hellaswag|0":"hellaswag",
         "custom|commonsense_qa|0": "commonsense_qa",
         "custom|openbookqa|0": "openbookqa",
         "custom|piqa|0": "piqa",
         "custom|siqa|0": "siqa",
         "custom|mmlu:_average|0": "mmlu",
         "custom|winogrande|0": "winogrande",
}



In [4]:
def extract_results(result_files, recalc_mean=False):
    data = []
    for f in result_files:
        splitted = f.split("/")
        #print(splitted)
        register = splitted[-3] #splitted[-2].split("_iter_")[0]
        step = splitted[-2].split("_")[-1] #splitted[-2].replace(f'{register}_iter_', "")
        step=int(step)
        #print(register)
        #print(step)
        with open(f, 'r') as result:
            j = json.load(result)
            results = {"step":int(step)}
            if step > 50000:
                continue
            results_all = j["results"]["all"]
            results = {**results, **results_all}
            for task, task_name in tasks.items():
                r = {k+f"_{task_name}":v for k,v in j["results"][task].items()}
                results = {**results, **r}
            #print(results)
            df = pd.DataFrame.from_dict({register:{"step":int(step), **results}})
            data.append(df.T)
            #print(register, j["results"]["all"])
            #data[register] = {step: j["results"]["all"]}

    df = pd.concat(data)
    df = df.reset_index()
    df = df.rename(columns={"index":"register"})
    # problem: step does not go to correct place on the plot
    # sort it as numerical, then make it categorical so plotting works
    # ordered=True does nothing here because plotly does not respect it; only sorting works
    df=df.sort_values("step")
    df["tokens"] = df["step"]*2.1e6
    #df["step"] = pd.Categorical(df['step'], categories=sorted(df['step'].astype(int).unique()), ordered=True)
    df["step"]= df['step'].apply(lambda x: str(round(x)))
    #df["tokens"]= df['tokens'].apply(lambda x: millify(x))
    if recalc_mean:
        df["acc_norm_original"] = df["acc_norm"]
        #df["acc_norm"] = df[["acc_norm_hellaswag", "acc_norm_openbookqa", "acc_norm_piqa", "acc_norm_arc_easy"]].mean(axis=1)
        df["acc_norm"] = df[[f"acc_norm_{taskname}" for taskname in tasks.values()]].mean(axis=1)
        df["stderr_norm"] = df[[f"acc_norm_stderr_{taskname}" for taskname in tasks.values()]].apply(lambda x: x**2).sum(axis=1)
        df["stderr_norm"] = df["stderr_norm"].apply(lambda x: math.sqrt(x))
    return df

df1 = extract_results(result_files, recalc_mean=True)

In [5]:
df = df1.sort_values(["register", "tokens"]).reset_index()
display(df)
print(df.columns)


index register       acc  acc_arc_challenge  acc_arc_easy  \
0      279       HI  0.245950              0.171         0.307   
1      265       HI  0.252454              0.182         0.369   
2      259       HI  0.257911              0.194         0.378   
3      281       HI  0.258030              0.177         0.399   
4      272       HI  0.260565              0.199         0.407   
..     ...      ...       ...                ...           ...   
949    140       ne  0.284349              0.233         0.482   
950    102       ne  0.283513              0.243         0.496   
951    115       ne  0.287017              0.235         0.480   
952    124       ne  0.284679              0.241         0.482   
953    127       ne  0.284346              0.236         0.485   

     acc_commonsense_qa  acc_hellaswag  acc_mmlu  acc_norm  \
0                 0.252          0.296  0.233294  0.351006   
1                 0.265          0.347  0.236395  0.377155   
2                 0.306          0.380  0.241425  0.388144   
3                 0.294          0.380  0.240596  0.400953   
4                 0.301          0.397  0.242293  0.406407   
..                  ...            ...       ...       ...   
949               0.340          0.374  0.267398  0.411706   
950               0.332          0.380  0.266409  0.414428   
951               0.331          0.379  0.270230  0.414604   
952               0.335          0.382  0.267915  0.416693   
953               0.331          0.372  0.267851  0.417933   

     acc_norm_arc_challenge  ...  acc_stderr_mmlu  acc_stderr_openbookqa  \
0                     0.222  ...         0.031361               0.016158   
1                     0.208  ...         0.031445               0.016244   
2                     0.235  ...         0.031593               0.016244   
3                     0.220  ...         0.031554               0.016894   
4                     0.242  ...         0.031707               0.016328   
..                      ...  ...              ...                    ...   
949                   0.267  ...         0.032736               0.018170   
950                   0.265  ...         0.032717               0.017491   
951                   0.270  ...         0.032892               0.018039   
952                   0.269  ...         0.032804               0.017771   
953                   0.280  ...         0.032775               0.017771   

     acc_stderr_piqa  acc_stderr_siqa  acc_stderr_winogrande  acc_winogrande  \
0           0.015071         0.015196               0.015819           0.496   
1           0.014633         0.015460               0.015787           0.532   
2           0.014356         0.015275               0.015817           0.509   
3           0.014013         0.015333               0.015796           0.527   
4           0.013825         0.015325               0.015755           0.545   
..               ...              ...                    ...             ...   
949         0.015130         0.015453               0.015685           0.565   
950         0.015241         0.015512               0.015672           0.568   
951         0.015081         0.015473               0.015631           0.577   
952         0.015177         0.015453               0.015693           0.563   
953         0.015120         0.015460               0.015727           0.554   

      step        tokens  acc_norm_original  stderr_norm  
0     1000  2.100000e+09           0.264036     0.054150  
1     2000  4.200000e+09           0.273118     0.054744  
2     3000  6.300000e+09           0.274549     0.054673  
3     4000  8.400000e+09           0.277428     0.055073  
4     5000  1.050000e+10           0.276535     0.054875  
..     ...           ...                ...          ...  
949  46000  9.660000e+10           0.301991     0.056417  
950  47000  9.870000e+10           0.303657     0.056491  
951  48000  1.008000e+11           0.303319     0.056481  
952

Index(['index', 'register', 'acc', 'acc_arc_challenge', 'acc_arc_easy',
       'acc_commonsense_qa', 'acc_hellaswag', 'acc_mmlu', 'acc_norm',
       'acc_norm_arc_challenge', 'acc_norm_arc_easy',
       'acc_norm_commonsense_qa', 'acc_norm_hellaswag', 'acc_norm_mmlu',
       'acc_norm_openbookqa', 'acc_norm_piqa', 'acc_norm_siqa',
       'acc_norm_stderr', 'acc_norm_stderr_arc_challenge',
       'acc_norm_stderr_arc_easy', 'acc_norm_stderr_commonsense_qa',
       'acc_norm_stderr_hellaswag', 'acc_norm_stderr_mmlu',
       'acc_norm_stderr_openbookqa', 'acc_norm_stderr_piqa',
       'acc_norm_stderr_siqa', 'acc_norm_stderr_winogrande',
       'acc_norm_winogrande', 'acc_openbookqa', 'acc_piqa', 'acc_siqa',
       'acc_stderr', 'acc_stderr_arc_challenge', 'acc_stderr_arc_easy',
       'acc_stderr_commonsense_qa', 'acc_stderr_hellaswag', 'acc_stderr_mmlu',
       'acc_stderr_openbookqa', 'acc_stderr_piqa', 'acc_stderr_siqa',
       'acc_stderr_winogrande', 'acc_winogrande', 'step', 'token

## Rolling average to make the line plots more readable

In [6]:
# rolling average over how many steps?

unique_registers = np.unique(df["register"])
print(unique_registers)
n = 3

def rolling_average(df, register, n=5):
    df_p = df[df.register==register].rolling(n, center=True, axis=0).mean()
    return df_p


dfs_rolled = []
for register in unique_registers:
    #print(register)
    p = rolling_average(df, register, n=n)
    p["register"]=register
    dfs_rolled.append(p)

df_rolled = pd.concat(dfs_rolled, axis=0).dropna()

display(df_rolled)
#display(df_rolled[df_rolled.register=="HI-IN"])




['HI' 'HI-IN' 'HI-IN_HI_dtp' 'HI-IN_HI_dtp_NA_OP' 'HI-IN_HI_dtp_NA_OP_ID'
 'HI-IN_HI_dtp_NA_OP_ID_SP' 'HI-IN_HI_dtp_OP' 'ID' 'IN' 'IP' 'LY' 'MT'
 'NA' 'OP' 'SP' 'dtp' 'fineweb' 'hplt-v2-dedup' 'ne']


index       acc  acc_arc_challenge  acc_arc_easy  \
1    267.666667  0.252105           0.182333      0.351333   
2    268.333333  0.256132           0.184333      0.382000   
3    270.666667  0.258835           0.190000      0.394667   
4    278.333333  0.260395           0.190000      0.406333   
5    272.000000  0.261869           0.201667      0.415667   
..          ...       ...                ...           ...   
948  138.000000  0.284413           0.234000      0.490000   
949  128.333333  0.283880           0.236333      0.487667   
950  119.000000  0.284960           0.237000      0.486000   
951  113.666667  0.285070           0.239667      0.486000   
952  122.000000  0.285348           0.237333      0.482333   

     acc_commonsense_qa  acc_hellaswag  acc_mmlu  acc_norm  \
1              0.274333       0.341000  0.237038  0.372102   
2              0.288333       0.369000  0.239472  0.388751   
3              0.300333       0.385667  0.241438  0.398501   
4              0.303000       0.395667  0.242415  0.405845   
5              0.314667       0.407667  0.243178  0.408728   
..                  ...            ...       ...       ...   
948            0.342667       0.371667  0.267593  0.413454   
949            0.340667       0.375667  0.266997  0.414122   
950            0.334333       0.377667  0.268013  0.413579   
951            0.332667       0.380333  0.268185  0.415242   
952            0.332333       0.377667  0.268665  0.416410   

     acc_norm_arc_challenge  acc_norm_arc_easy  ...  acc_stderr_mmlu  \
1                  0.221667           0.352333  ...         0.031466   
2                  0.221000           0.381667  ...         0.031530   
3                  0.232333           0.396667  ...         0.031618   
4                  0.234333           0.403667  ...         0.031689   
5                  0.240333           0.408000  ...         0.031741   
..                      ...                ...  ...              ...   
948                0.262667           0.478000  ...         0.032771   
949                0.264667           0.473667  ...         0.032745   
950                0.267333           0.470667  ...         0.032782   
951                0.268000           0.471333  ...         0.032804   
952                0.273000           0.470333  ...         0.032824   

     acc_stderr_openbookqa  acc_stderr_piqa  acc_stderr_siqa  \
1                 0.016215         0.014687         0.015310   
2                 0.016460         0.014334         0.015356   
3                 0.016489         0.014065         0.015311   
4                 0.016626         0.013951         0.015338   
5                 0.016652         0.013905         0.015385   
..                     ...              ...              ...   
948               0.017391         0.015183         0.015488   
949               0.017439         0.015189         0.015497   
950               0.017900         0.015150         0.015480   
951               0.017767         0.015166         0.015480   
952               0.017860         0.015126         0.015462   

     acc_stderr_winogrande  acc_winogrande        tokens  acc_norm_original  \
1                 0.015807        0.512333  4.200000e+09           0.270567   
2                 0.015800        0.522667  6.300000e+09           0.275032   
3                 0.015789        0.527000  8.400000e+09           0.276171   
4                 0.015780        0.534333  1.050000e+10           0.277846   
5                 0.015783        0.532333  1.260000e+10           0.278198   
..                     ...             ...           ...                ...   
948               0.015657        0.571000  9.450000e+10           0.301135   
949               0.015679        0.566333  9.660000e+10           0.301816   
950               0.015663        0.570000  9.870000e+10           0.302989   
951               0.015665        0.569333  1.008000e+11           0.303470   
952              

# Actual final plotting

Here I chose the colormaps, put dashed lines for epoch limits, etc. Using the rolled average as before since rugged lines are hard to follow by eye.


In [7]:
# constants and helpers

organized_registers=['HI-IN_HI_dtp','HI-IN_HI_dtp_OP','HI-IN_HI_dtp_NA_OP','HI-IN_HI_dtp_NA_OP_ID','HI-IN_HI_dtp_NA_OP_ID_SP','fineweb','HI-IN','hplt-v2-dedup','dtp','HI','OP','NA','IN','ID','SP','ne','IP','MT','LY']
organized_registers2=['HI-IN_HI_dtp_OP','HI-IN_HI_dtp_NA_OP','HI-IN_HI_dtp','HI-IN_HI_dtp_NA_OP_ID','HI-IN_HI_dtp_NA_OP_ID_SP','fineweb','HI-IN','hplt-v2-dedup','dtp','HI','OP','NA','IN','ID','SP','ne','IP','MT','LY']
vanilla_registers=['HI-IN','dtp','HI','OP','IN','NA','ID','SP','ne','IP','MT','LY']
baselines=["fineweb", "hplt-v2-dedup"]
combinations = ['HI-IN_HI_dtp','HI-IN_HI_dtp_OP','HI-IN_HI_dtp_NA_OP','HI-IN_HI_dtp_NA_OP_ID','HI-IN_HI_dtp_NA_OP_ID_SP']


register_name_map = {'HI-IN_HI_dtp_OP': "HI-IN-HI-dtp-OP",
                     'HI-IN_HI_dtp_NA_OP': "HI-IN-HI-dtp-OP-NA",
                     'HI-IN_HI_dtp': "HI-IN-HI-dtp",
                     'HI-IN_HI_dtp_NA_OP_ID':"HI-IN-HI-dtp-OP-NA-ID",
                     'HI-IN_HI_dtp_NA_OP_ID_SP': "HI-IN-HI-dtp-OP-NA-ID-SP",
                     'hplt-v2-dedup': "All Registers (full HPLT v2)",#"HPLT v2",
                     'fineweb': "FineWeb",
                     'HI-IN': "Instructive-Informational",
                     'HI': "How-to-Instructions",
                     'ID': "Interactive Discussion",
                     'IN': "Informational Description",
                     "IP": "Informational Persuasion",
                     "LY": "Lyrical",
                     "MT": "Machine Translation",
                     "NA": "Narrative",
                     "OP": "Opinion",
                     "SP": "Spoken",
                     "ne": "News",
                     "dtp": "Description"}

def create_colormap(vanilla_cmap_name="Turbo", baseline_cmap_name="Bluered", combinations_cmap_name="Haline"):
    global vanilla_registers
    global baselines
    global combinations

    c_map={}
    angles_v = np.linspace(0, 1, len(vanilla_registers))
    angles_b = np.linspace(0, 1, len(baselines))
    angles_c = np.linspace(0, 1, len(combinations)+1) # +1 because the map is cyclic
    #np.random.seed(0)
    #random_index=np.random.permutation(len(unique_registers))
    color_scale_v = px.colors.sample_colorscale(vanilla_cmap_name, angles_v)
    color_scale_b = px.colors.sample_colorscale(baseline_cmap_name, angles_b)
    color_scale_c = px.colors.sample_colorscale(combinations_cmap_name, angles_c)

    for i, register in enumerate(vanilla_registers):
        c_map[register] = color_scale_v[i].replace("rgb", "rgba").replace(")", ", 1)")
    for i, register in enumerate(baselines):
        c_map[register] = color_scale_b[i].replace("rgb", "rgba").replace(")", ", 1)")
    for i, register in enumerate(combinations):
        c_map[register] = color_scale_c[i].replace("rgb", "rgba").replace(")", ", 1)")

    return c_map

def change_opacity(c_map, label, focus):
    if label in focus:
        return c_map[label]
    else:
        return c_map[label].replace(", 1)", ", 0.7)")

## Regular line plots

In [30]:


def plot(df, focus, exclude=[], dash=[], figname="plot"):
    fig = px.line()
        
    c_map = create_colormap()
    #print(c_map)
    # Group by label and plot each group with a different color
    for label in organized_registers2:
        if label in exclude:
            continue
        if label in focus:
            linewidth=3
        else:
            linewidth=2
        label_data = df[df['register'] == label]
        if label in dash:
            dash_type="dash"
        else:
            dash_type="solid"


        # epoch size
        if label =="LY":
            limit=20e9 
        elif label=="SP": 
            limit =32e9 
        elif label=="HI-IN":
            limit=70e9
        else: 
            limit = 103e9   # over 100B so that we get the 100B line on the plot
        
        fig.add_trace(
            go.Scatter(
                x=label_data[label_data.tokens<=limit]['tokens'], 
                y=label_data[label_data.tokens<=limit]["acc_norm"], 
                mode='lines', 
                showlegend=True,
                name=f'{register_name_map.get(label, label)}',  # get new name if defined, else just the register label
                legendgroup=f'{label}',
                line=dict(color=change_opacity(c_map, label, focus), width=linewidth, dash = dash_type)
            ),
            row=1, col=1
        )
        fig.add_trace(
            go.Scatter(
                x=label_data[label_data.tokens>limit-2e9]['tokens'], # -2e9 is the step size, this way we connect the plots to above
                y=label_data[label_data.tokens>limit-2e9]["acc_norm"], 
                mode='lines', 
                showlegend=False,
                name=f'{register_name_map.get(label, label)}',  # get new name if defined, else just the register label
                legendgroup=f'{label}',
                line=dict(color=change_opacity(c_map, label, focus), dash="dot", width=linewidth)
            ),
            row=1, col=1
        )

    # Update layout for better appearance
    fig.update_layout(
        title="",
        height=600,  # Adjust the height of the plot
        width=900,
        font_family="Computer Modern",
        font_size=20,
        xaxis=dict(
            title=dict(
                text="Training tokens"
            )
        ),
        yaxis=dict(
            title=dict(
                text="Average accuracy"
            )
        ),
        showlegend=True,  # Show legend
        template="none",
        legend_tracegroupgap=10,
        #margin=dict(l=50, r=10, t=20, b=30)
    )
    fig.add_annotation(x=103e9, y=0.34,
            text="Dotted lines indicate training past one epoch",
            showarrow=False,
            xanchor="right",
            font=dict(color="gray")
    )
    fig.write_image(f"sampolle/{figname}.png", scale=3)
    fig.show()

    
plot(df_rolled, vanilla_registers+["hplt-v2-dedup"], exclude=combinations+["fineweb"], figname="registers")
plot(df_rolled, combinations+baselines, exclude=vanilla_registers, figname="comb-and-baseline-only")
#plot(df_rolled, vanilla_registers+["hplt-v2-dedup"], figname="all-in-one")
#plot(df_rolled, combinations+baselines, figname="combinations")
#plot(df_rolled, organized_registers, figname="all")
#plot(df_rolled, organized_registers, figname="all", dash=combinations+["fineweb"])

## Line plots, separated benchmarks

In [9]:
random_baselines={'acc_norm_arc_easy':1/4.0,
                  'acc_norm_arc_challenge':1/4.0,
                  'acc_norm_hellaswag': 1/4.0,
                  'acc_norm_mmlu': 1/4.0,
                  'acc_norm_siqa': 1/3.0,
                  'acc_norm_piqa': 1/2.0,
                  'acc_norm_winogrande': 1/2.0,
                  'acc_norm_commonsense_qa': 1/5.0,
                  'acc_norm_openbookqa': 1/4.0
}
#1/4 for ARCs, HellaSwag, MMLU, and OpenBookQA 1/3 for SIQA, 1/2 for PIQA and WinoGrande, 1/5 for commonsenseQA


def plot_per_task(df, figname="plot"):
    global register_name_map
    fig = make_subplots(
        rows=5, cols=2, 
        subplot_titles=["ARC Easy", "HellaSwag", "MMLU", "ARC Challenge", "SIQA", "PIQA", "WinoGrande", "CommonsenseQA", "OpenBookQA"],
        #x_title="Tokens",
        #y_title="Accuracy score",
        #shared_xaxes=True,  # Share the x-axis across all subplots
        vertical_spacing=0.05,  # Adjust space between subplots
        #horizontal_spacing=0.08
    )
    c_map = create_colormap()
    # List of accuracy columns
    accuracy_columns = ['acc_norm_arc_easy', 'acc_norm_hellaswag', 'acc_norm_mmlu', 'acc_norm_arc_challenge', 'acc_norm_siqa', 'acc_norm_piqa', 'acc_norm_winogrande', 'acc_norm_commonsense_qa', 'acc_norm_openbookqa']

    # Loop over each accuracy metric and add traces to the subplots
    for i, accuracy_col in enumerate(accuracy_columns):
        # these are for baseline presentations
        add_baseline_rectangle=False
        x0, y0, x1, y1 = (0,1,0,1)

        row = int(i/2)+1 #(i // 5) + 1  # Determine the row for the subplot (1 2 or 3)
        col = (i % 2) + 1   # Determine the column for the subplot (1 2 or 3)
        #print(f'{accuracy_col}; row {row} col {col}')
        # Group by label and plot each group with a different color
        for label in organized_registers:
            label_data = df[df['register'] == label]
            dash_type = "solid" if label in combinations else "solid"
            fig.add_trace(
                go.Scatter(
                    x=label_data['tokens'], 
                    y=label_data[accuracy_col], 
                    mode='lines', 
                    showlegend=True if row==1 and col==1 else False,
                    name=f'{register_name_map.get(label, label)}', 
                    legendgroup=f'{label}',
                    line=dict(color=c_map[label], width=1.5, dash=dash_type)
                ),
                row=row, col=col
            )
            if label_data.min(axis=0)[accuracy_col] < random_baselines[accuracy_col]: #results are worse than baseline
                add_baseline_rectangle = True 
                x0 = label_data['tokens'].iloc[0] # these are static
                x1 = label_data['tokens'].iloc[-1] # does not matter if they are changed multiple times :)
                y0 = label_data.min(axis=0)[accuracy_col] if label_data.min(axis=0)[accuracy_col] < y0 else y0
                y1 = random_baselines[accuracy_col] # this is also static
                #print(f"Adding baseline thingy on {label} and {accuracy_col}, {label_data.min(axis=0)[accuracy_col]} < {random_baselines[accuracy_col]}")
                
        if add_baseline_rectangle:
            fig.add_shape(
                type="rect",
                x0=x0, 
                x1=x1,
                y0=y0,
                y1=y1,
                fillcolor="gray",
                line_color="gray",
                opacity=0.2,
                row=row, col=col
                )
                
                

    # Update layout for better appearance
    fig.update_layout(
        title="",#"Accuracy Metrics by Task and Register",
        height=1300,  # Adjust the height of the plot
        width=900,
        font=dict(family="Computer Modern", size=16),
        legend_font_size=20,
        title_font_size=20,
        #title_font_size=40,
        showlegend=True,  # Show legend
        template="none",
        legend_tracegroupgap=15,
        margin=dict(l=50, r=50, t=20, b=20)
    )
    fig.update_annotations(font_size=20) #subplot titles are annotations
    fig.write_image(f"sampolle/{figname}.png", scale=3)


    # Show the plot
    fig.show()

plot_per_task(df_rolled, figname="per_task")

## Line plots side by side

In [10]:
def plot_side_by_side2(df, first_plot_columns, second_plot_columns, figname="plot"):
    global register_name_map
    fig = make_subplots(
        rows=1, cols=2, 
        subplot_titles=["", ""],
        #x_title="Tokens",
        #y_title="Accuracy",
        #shared_xaxes=True,  # Share the x-axis across all subplots
        horizontal_spacing=0.08,  # Adjust space between subplots
    )
    c_map = create_colormap()
    accuracy_col="acc_norm"
    # List of accuracy columns
    #accuracy_columns = ['acc_norm_arc_easy', 'acc_norm_hellaswag', 'acc_norm_mmlu', 'acc_norm_arc_challenge', 'acc_norm_siqa', 'acc_norm_piqa', 'acc_norm_winogrande', 'acc_norm_commonsense_qa', 'acc_norm_openbookqa']

    
    # Loop over each accuracy metric and add traces to the subplots
    for label in organized_registers:
        for i, focus_registers in enumerate([first_plot_columns,first_plot_columns+second_plot_columns]): 
            row = 1
            col = i+1 
            #print(row, col)
            
            # Group by label and plot each group with a different color
        
            if label not in focus_registers:
                continue
            if label =="LY":
                limit=20e9 
            elif label=="SP": 
                limit =32e9 
            elif label=="HI-IN":
                limit=70e9
            else: 
                limit = 103e9
            label_data = df[df['register'] == label]
            dash_type="solid"
            width=3
            focus=focus_registers
            if col == 2:
                focus = second_plot_columns
                if label in first_plot_columns and label != "HPLT-v2-dedup":
                    width=2
            #if col == 2:
            #    focus = second_plot_columns
            #    dash_type = "solid"
            #    if label in first_plot_columns:
            #        width = 1
            fig.add_trace(
                go.Scatter(
                    x=label_data[label_data.tokens<limit]['tokens'], 
                    y=label_data[label_data.tokens<limit][accuracy_col], 
                    mode='lines', 
                    showlegend=True if label in focus_registers else False,
                    name=f'{register_name_map.get(label, label)}', 
                    legendgroup=f'{label}',
                    line=dict(color=change_opacity(c_map, label, focus), width=width),
                ),
                row=row, col=col
            )
            fig.add_trace(
            go.Scatter(
                x=label_data[label_data.tokens>limit-2e9]['tokens'], # -2e9 is the step size, this way we connect the plots to above
                y=label_data[label_data.tokens>limit-2e9]["acc_norm"], 
                mode='lines', 
                showlegend=False,
                name=f'{register_name_map.get(label, label)}',  # get new name if defined, else just the register label
                legendgroup=f'{label}',
                line=dict(color=change_opacity(c_map, label, focus), dash="dot", width=2)
            ),
            row=row, col=col
        )
                    


    names = set()
    fig.for_each_trace(
        lambda trace:
            trace.update(showlegend=False)
            if (trace.name in names) else names.add(trace.name))
  

    # Update layout for better appearance
    fig.update_layout(
        title="",#"Accuracy Metrics by Task and Register",
        height=650,  # Adjust the height of the plot
        width=1300,
        showlegend=True,  # Show legend
        template="none",
        legend_tracegroupgap=10,
        margin=dict(l=30, r=10, t=20, b=20),

    )
    fig.write_image(f"sampolle/{figname}.png", scale=3)


    # Show the plot
    fig.show()

#plot_side_by_side2(df_rolled, vanilla_registers+["hplt-v2-dedup"], combinations+["fineweb"]+["hplt-v2-dedup"], figname="side-by-side" )

# Bar plots


In [11]:
# Assuming df is your pandas DataFrame and colormap is the dictionary
# Example colormap (replace this with your actual colormap)


def create_colormap(vanilla_cmap_name="Turbo", baseline_cmap_name="BlueRed", combinations_cmap_name="Haline"):
    global vanilla_registers
    global baselines
    global combinations

    c_map={}
    angles_v = np.linspace(0, 1, len(vanilla_registers))
    angles_b = np.linspace(0, 1, len(baselines))
    angles_c = np.linspace(0, 1, len(combinations)+1) # +1 because the map is cyclic
    #np.random.seed(0)
    #random_index=np.random.permutation(len(unique_registers))
    color_scale_v = px.colors.sample_colorscale(vanilla_cmap_name, angles_v)
    color_scale_b = px.colors.sample_colorscale(baseline_cmap_name, angles_b)
    color_scale_c = px.colors.sample_colorscale(combinations_cmap_name, angles_c)

    for i, register in enumerate(vanilla_registers):
        c_map[register] = color_scale_v[i].replace("rgb", "rgba").replace(")", ", 1)")
    for i, register in enumerate(baselines):
        c_map[register] = color_scale_b[i].replace("rgb", "rgba").replace(")", ", 1)")
    for i, register in enumerate(combinations):
        c_map[register] = color_scale_c[i].replace("rgb", "rgba").replace(")", ", 1)")

    return c_map

    
colormap = create_colormap() # Example dictionary
label_order = organized_registers # Specify the order of labels

# Filter the dataframe to select rows where step == 50000
filtered_df = df[df['step'] == "50000"]

# Initialize an empty list to store the bar traces
traces = []

# Loop over the label names in the specified order
for label in label_order[::-1]:
    # Get the corresponding data for the current label
    label_data = filtered_df[filtered_df['register'] == label]
    #print(label_data)
    
    # Get the average 'acc_norm' (or other aggregation method)
    acc_norm_value = label_data['acc_norm']  # Or other aggregation if needed'
    error = label_data["stderr_norm"]
    #print(acc_norm_value)
    
    # Add the bar for this label to the traces list
    traces.append(go.Bar(
        x=[f'{register_name_map.get(label, label)}'],  # x-axis is the label
        y=acc_norm_value,  # y-axis is the 'acc_norm' value
        name=f'{register_name_map.get(label, label)}',  # Label for the legend
        marker_color=colormap.get(label, 'gray'),  # Get color from colormap (default to gray if not found)
        error_y=dict(type="data", array=[error],visible=True)
    ))

# Create the figure with all bars
fig = go.Figure(data=traces)

# Update layout to add title and axis labels
fig.update_layout(
    title="",#'Acc Norm by Label at Step 50000',
    xaxis_title="",#'Label',
    yaxis_title="",#'Acc Norm',
    showlegend=False,
    width=1000,
    height=600,
    template="none",
    margin=dict(l=30, r=60, t=20, b=100)
)

fig.write_image(f"sampolle/bar_average.png", scale=3)
# Show the plot
fig.show()

In [12]:



fig = make_subplots(
    rows=3, cols=3, 
    subplot_titles=["ARC Easy", "HellaSwag", "MMLU", "ARC Challenge", "SIQA", "PIQA", "WinoGrande", "CommonsenseQA", "OpenBookQA"],
    #x_title="Tokens",
    #y_title="Accuracy score",
    #shared_xaxes=True,  # Share the x-axis across all subplots
    vertical_spacing=0.1,  # Adjust space between subplots
    horizontal_spacing=0.03
)
c_map = create_colormap()
# List of accuracy columns
accuracy_columns = ['acc_norm_arc_easy', 'acc_norm_hellaswag', 'acc_norm_mmlu', 'acc_norm_arc_challenge', 'acc_norm_siqa', 'acc_norm_piqa', 'acc_norm_winogrande', 'acc_norm_commonsense_qa', 'acc_norm_openbookqa']

# Loop over each accuracy metric and add traces to the subplots
for i, accuracy_col in enumerate(accuracy_columns):
    # these are for baseline presentations
    #add_baseline_rectangle=False
    #x0, y0, x1, y1 = (0,1,0,1)
    
    row = (i // 3) + 1  
    col = (i % 3) + 1      
    
    fig.add_trace(go.Scatter(y=[random_baselines[accuracy_col]]*21, 
                             mode="lines",
                             line=dict(color='gray'),
                             showlegend=False,
                             ),
                             row=row, 
                             col=col,
            )
    
    # Group by label and plot each group with a different color
    
    for label in organized_registers:
        label_data = filtered_df[filtered_df['register'] == label]
        acc_norm_value = label_data[accuracy_col]

        fig.add_trace(
            go.Bar(
                x=[f'{register_name_map.get(label, label)}'],  # x-axis is the label
                y=acc_norm_value,  # y-axis is the 'acc_norm' value
                name=f'{register_name_map.get(label, label)}',  # Label for the legend
                marker_color=colormap.get(label, 'gray'),  # Get color from colormap (default to gray if not found)
                showlegend=True if col==1 and row==1 else False,
                #legendgroup = group,
                #xaxis=dict(
                #    showticklabels=show_tick),
            ),
            row=row, col=col
        )
            
            

# Update layout for better appearance
fig.update_layout(
    title="",#"Accuracy Metrics by Task and Register",
    height=450,  # Adjust the height of the plot
    width=850,
    showlegend=True,  # Show legend
    template="none",
    #legend_tracegroupgap=100,
    margin=dict(l=30, r=20, t=20, b=20),
    #legend=dict(orientation="h"),
    #legend_tracegroupgap=50,
)

fig.update_xaxes(showticklabels=False) # hide all the xticks
#fig.update_xaxes(showticklabels=True, row=3, col=1)
#fig.update_xaxes(showticklabels=True, row=3, col=2)
#fig.update_xaxes(showticklabels=True, row=3, col=3)
fig.write_image(f"sampolle/bar_per_task.png", scale=3)


# Show the plot
fig.show()

#plot_per_task(df, figname="per_task")

## Example for a Range plot

from https://stackoverflow.com/questions/63213527/is-there-a-way-to-create-range-plot-in-python-using-plotly

## Doing it for register data

In [13]:
        
def plot_range(df, filename="range_average", omit=[], height=600,left_margin=50):
        #display(df)
        df_min_max = df[(df["step"] == "1000") | (df["step"] =="50000")]
        #print(df_min_max)


        def change_opacity2(c_map, label, value=0.1):
                return c_map[label].replace(", 1)", ", "+str(value)+")")

        def change_to_lighter(c_map, label, value = 1):
                numbers_only = c_map[label].replace("rgba", "")
                re,gr,bl,op = eval(numbers_only)
                re+=(150)*((255-re)/255)
                gr+=(150)*((255-gr)/255)
                bl+=(150)*((255-gr)/255)
                new_color = 'rgba('+ f"{min(250, re)},{min(250,gr)},{min(250,bl)},{value}"+')'
                return new_color


        cmap=create_colormap()
        fig = go.Figure()

        for i, r in enumerate(organized_registers[::-1]):  #(combinations+["fineweb","hplt-v2-dedup"])[::-1]
                if r in omit:
                        continue
                values = df_min_max[df_min_max.register == r]
                maxv, minv = max(values['acc_norm']), min(values["acc_norm"])
                #print(np.linspace(minv, maxv, 10))
                #print(10*[r])
                #print(f"{[change_to_lighter(cmap, r), cmap[r]]}")
                fig.add_trace(go.Scatter(x = np.linspace(minv, maxv, 500),
                                        y = 500*[register_name_map.get(r,r)],
                                        mode = "markers",
                                        marker = {'color':np.linspace(minv, maxv, 500),
                                                'colorscale':['lightgray', cmap[r]],
                                                'size': 8
                                                }
                                        )
                                )
                # arrows to the end, if needed
                #fig.add_trace(go.Scatter(x = [maxv+0.002],
                #                         y = [register_name_map.get(r,r)],
                #                         mode = "markers",
                #                         marker_symbol="arrow-right",
                #                         marker = {'color': cmap[r], "size":15}
                #                        )
                #                )
                
        fig.update_layout(
        title="",#"Accuracy Metrics by Task and Register",
        height=height,  # Adjust the height of the plot
        width=1000,
        font_family="Computer Modern",
        font_size=18,
        showlegend=False,  # Show legend
        template="none",
        #legend_tracegroupgap=100,
        margin=dict(l=left_margin, r=0, t=20, b=40),
        #legend=dict(orientation="h"),
        #legend_tracegroupgap=50,
        )  
        fig.write_image(f"sampolle/{filename}.png", scale=3)

        fig.show()

plot_range(df, filename="range_individual", omit=combinations+["fineweb"],height=400, left_margin=200)
plot_range(df, filename="range_recombinations", omit=vanilla_registers, height=250, left_margin=220)

In [14]:
accuracy_columns = ['acc_norm_arc_easy', 'acc_norm_hellaswag', 'acc_norm_mmlu', 'acc_norm_arc_challenge', 'acc_norm_siqa', 'acc_norm_piqa', 'acc_norm_winogrande', 'acc_norm_commonsense_qa', 'acc_norm_openbookqa']
df_min_max = df[(df["step"] == "1000") | (df["step"] =="50000")]
cmap=create_colormap()
random_baselines={'acc_norm_arc_easy':1/4.0,
                  'acc_norm_arc_challenge':1/4.0,
                  'acc_norm_hellaswag': 1/4.0,
                  'acc_norm_mmlu': 1/4.0,
                  'acc_norm_siqa': 1/3.0,
                  'acc_norm_piqa': 1/2.0,
                  'acc_norm_winogrande': 1/2.0,
                  'acc_norm_commonsense_qa': 1/5.0,
                  'acc_norm_openbookqa': 1/4.0
}


fig = make_subplots(
    rows=3, cols=3, 
    subplot_titles=["ARC Easy", "HellaSwag", "MMLU", "ARC Challenge", "SIQA", "PIQA", "WinoGrande", "CommonsenseQA", "OpenBookQA"],
    #x_title="Tokens",
    #y_title="Accuracy score",
    #shared_xaxes=True,  # Share the x-axis across all subplots
    vertical_spacing=0.1,  # Adjust space between subplots
    horizontal_spacing=0.03
)
# Loop over each accuracy metric and add traces to the subplots
for i, accuracy_col in enumerate(accuracy_columns):
    # these are for baseline presentations
    #add_baseline_rectangle=False
    #x0, y0, x1, y1 = (0,1,0,1)
    
    row = (i // 3) + 1  # Determine the row for the subplot (1 2 or 3)
    col = (i % 3) + 1   # Determine the column for the subplot (1 2 or 3)

    # put random guess threshold where needed
    if accuracy_col not in ["acc_norm_arc_easy","acc_norm_hellaswag","acc_norm_siqa", "acc_norm_piqa", "acc_norm_commonsense_qa"]:
        fig.add_trace(go.Scatter(x=[random_baselines[accuracy_col]]*21, 
                             mode="lines",
                             line=dict(color='gray'),
                             showlegend=False,
                             ),
                             row=row, 
                             col=col,
            )
    
    
    # Group by label and plot each group with a different color
    
    for i, r in enumerate(organized_registers2[::-1]):
        values = df_min_max[df_min_max.register == r]
        maxv, minv = max(values[accuracy_col]), min(values[accuracy_col])
        #print(np.linspace(minv, maxv, 10))
        #print(10*[r])
        #print(f"{[change_to_lighter(cmap, r), cmap[r]]}")
        fig.add_trace(go.Scatter(x = np.linspace(maxv, minv, 100),
                                 y = 100*[register_name_map.get(r,r)],
                                 showlegend=True if col==1 and row == 1 else False,
                                 mode = "markers",
                                 name=register_name_map.get(r,r),
                                 legendgroup=r,
                                 marker = {'color':np.linspace(minv, maxv, 100),
                                           'colorscale':[ cmap[r],"lightgray"],
                                           'size': 4
                                           }
                                ),
                        row=row, col=col
                        )
        
fig.update_layout(
    title="",#"Accuracy Metrics by Task and Register",
    #font_family="Computer Modern",
    #font_size=18,
    font=dict(family="Computer Modern", size=16),
    height=550,  # Adjust the height of the plot
    width=800,
    #showlegend=False,  # Show legend
    template="none",
    legend_tracegroupgap=30,
    margin=dict(l=20, r=10, t=20, b=30),
    legend={'traceorder':'reversed', 'itemsizing':"constant"},
    #legend=dict(orientation="h"),
    #legend_tracegroupgap=50,
)  
fig.update_annotations(font_size=18)
fig.update_yaxes(showticklabels=False)
fig.write_image(f"sampolle/range_per_task.png", scale=3)
fig.show()

## Latex table:



In [15]:
millnames = ['',' k',' M',' B',' T']
def millify(n):
    n = float(n)
    millidx = max(0,min(len(millnames)-1,
                        int(math.floor(0 if n == 0 else math.log10(abs(n))/3))))

    return '{:.0f}{}'.format(n / 10**(3 * millidx), millnames[millidx])


df_min_max = df[(df["step"] == "1000") | (df["step"] =="50000")]
to_latex= df_min_max[["register","step", "tokens", "acc_norm", "acc_norm_original", "acc_norm_stderr"]]

to_latex["register"] = to_latex["register"].map(lambda x: register_name_map.get(x,x))
to_latex["tokens"] = to_latex["tokens"].map(lambda x: millify(x))
to_latex = to_latex.sort_values(["register", "step"])
#display(to_latex)
#["register","step", "tokens", "acc_norm_original", "stderr_norm"]
print(to_latex.to_string(index=False))

                     register   step tokens  acc_norm  acc_norm_original  acc_norm_stderr
 All Registers (full HPLT v2)   1000    2 B  0.341536           0.265107         0.030274
 All Registers (full HPLT v2)  50000  105 B  0.457484           0.328140         0.032064
                  Description   1000    2 B  0.347940           0.268266         0.030463
                  Description  50000  105 B  0.452347           0.329816         0.032027
                      FineWeb   1000    2 B  0.348450           0.269707         0.030520
                      FineWeb  50000  105 B  0.465567           0.330767         0.031929
                 HI-IN-HI-dtp   1000    2 B  0.354339           0.265349         0.030291
                 HI-IN-HI-dtp  50000  105 B  0.465616           0.320815         0.031642
              HI-IN-HI-dtp-OP   1000    2 B  0.352104           0.267529         0.030357
              HI-IN-HI-dtp-OP  50000  105 B  0.475093           0.331857         0.032058
          

/users/mynttiam/.local/lib/python3.6/site-packages/ipykernel_launcher.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/users/mynttiam/.local/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

